In [1]:
#Purpose of this file: This is the final chart, an interactive visualisation, combining the findings from all previous charts.

import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt
import seaborn as sns
import folium
import datetime

# natgeo custom world map style
cust_tiles = 'https://server.arcgisonline.com/ArcGIS/rest/services/NatGeo_World_Map/MapServer/tile/{z}/{y}/{x}'
# Stuff requested to be entered by original map maker
cust_attr = 'Tiles &copy; Esri &mdash; National Geographic, Esri, DeLorme, NAVTEQ, UNEP-WCMC, USGS, NASA, ESA, METI, NRCAN, GEBCO, NOAA, iPC'

#Seaborn grid styles
sns.set_style('darkgrid')

#Remove chained assignments when assigning values to prevent further indexing
pd.options.mode.chained_assignment = None 

#Create data frame from CSV data
df = pd.read_csv(r'https://raw.githubusercontent.com/Whistlingwind/wk3-earthquake-assignment/main/modified_all_month.csv')

#Create additional columns for day, month, year to be able to aggregate by them
df['year'] = pd.DatetimeIndex(df['time']).year
df['month'] = pd.DatetimeIndex(df['time']).month
df['day'] = pd.DatetimeIndex(df['time']).day

#Ensure that day, month, year are integer data types to ensure we can apply mathmetical processing
df.year = df.year.astype('int')
df.month = df.month.astype('int')
df.day = df.day.astype('int')

#placeholder currently unused
#year_select = 2023
month_select = int(input("Enter the month you want to see: "))

#placeholder currently unused
#day_select = 1

#Create variable to hold month naming convention for visualisation header
month_name = 'August'

#Update month name, according to inputted month
if month_select == 8:
    month_name = 'August'
elif month_select == 9:
    month_name = 'September'

# filter by selected year
df_month = df.query('month == @month_select')

# get mean lat and lon of the selected data to use to center the plot
mean_lat = df_month.Latitude.mean()
mean_lon = df_month.Longitude.mean()

# make arrays for lat, lon, and magnitude
lat = np.asarray(df_month.Latitude)
lon = np.asarray(df_month.Longitude)
mag = np.asarray(df_month.mag)

# create the map
m= folium.Map(location=[mean_lat, mean_lon], 
                tiles = cust_tiles,
                attr = cust_attr,
                zoom_start=2)

# Instead of the default markers, create circle markers whose size is scaled by the magnitude
for idx in range(len(lat)):
    marker = folium.CircleMarker(
        location=[lat[idx],lon[idx]],
        radius=mag[idx]**5/2500,
        color='Red',
        popup=f"lat: {lat[idx]}, lon: {lon[idx]}",
        tooltip=f'Magnitude: {mag[idx]}')
    marker.add_to(m)

# Add a title to the map
t = f'Earthquakes in {month_name}'
title_html = '''
             <h3 align="center" style="font-size:16px"><b>{}</b></h3>
             '''.format(t) 
m.get_root().html.add_child(folium.Element(title_html))
m
